In [ ]:
%pylab inline

In [ ]:
import numpy as np
import scipy.sparse as sp

# Préparation des données
Récupérez l'archive http://files.grouplens.org/datasets/movielens/ml-100k.zip, sauvegardez-la dans le répertoire /donnees de votre machine, et décompressez-la.

Le jeu de données contient 100,000 notes (entre 1 et 5) données par 943 utilisateurs sur 1682 films.

Nous utiliserons pour ce TP:
+ Le fichier u.data qui contient la liste des diférentes notes données par les différents utilisateurs aux différents films
+ Le fichier u.item qui fournit des infirmations sur les films concernés (titre, année de sortie, genre,...) 

### Data matrix

In [ ]:
M = np.loadtxt('/donnees/ml-100k/u.data', dtype='int32')

In [ ]:
row = M[:,0] - 1
col = M[:,1] - 1
data = M[:,2]
X = sp.coo_matrix((data, (row , col))).toarray()

In [ ]:
figure(figsize=(35,12)); imshow(X, aspect='auto')

### Soustraction de la moyenne

In [ ]:
(m,n) = X.shape
X_new = np.zeros((m,n)) 
for i in range(m):
    indices = np.where(X[i,:]>0)
    X_new[i,indices] = X[i,indices] - mean(X[i,indices])


In [ ]:
figure(figsize=(35,12)); imshow(X_new, aspect='auto')

### Informations sur les films

Pour lire les données contenues dans u.item, vous devez utiliser un csv.reader :

In [ ]:
import csv

r = csv.reader(["unknown|Action|Adventure|Animation|Children's|Comedy|Crime|Documentary|Drama|Fantasy|Film-Noir|Horror|Musical|Mystery|Romance|Sci-Fi|Thriller|War|Western"], delimiter = '|')
for genre_header in r:
    print genre_header

In [ ]:
item_data = []
f = open("/donnees/ml-100k/u.item",'r')
reader = csv.reader(f, delimiter='|')
for row in reader:
    item_data += [row]
    
titre = {}
genre = {}
for i in range(len(item_data)):
    #print item_data[i][0]
    titre[i] = item_data[i][1]
    genre[i] = {}
    for j in range(19):
        if int(item_data[i][5+j]) == 1:
            genre[i][genre_header[j]] = 1

**Exo** : affichez le titre et le genre des dix premiers films de la liste.

### Analyse en Composantes Principales (ACP)

In [ ]:
C = np.cov(X_new)

In [ ]:
C.shape

Calcul des valeurs propres et des vecteurs propres 

In [ ]:
[L,V_acp] = np.linalg.eig(C)

Projection dans la nouvelle base

In [ ]:
Y_acp = V_acp.T.dot(X_new) 

Représentez les 100 premiers films de la base sur les deux ou trois premieres composantes en
utilisant les codes couleurs suivants : 
 + rouge pour action
 + bleu pour adventure
 + vert pour comedy
 + magenta pour drama
 + noir pour thriller

Conclusion?

### Reconstruction inverse

On souhaite représenter les films de la base à l'aide d'un nombre réduit de composantes.  
 + Combien de composantes sont nécessaires pour traduire 95% de la variance des données initiales?
 + Soit K le nombre de composantes déterminé précédemment. Reconstruisez la matrice des notes initiales a partir de ces K composantes. Quelle est l'erreur moyenne par rapport à la matrice de depart ?

### Décomposition en Valeurs Singulières (SVD)

In [ ]:
U_svd, s, V_svd = np.linalg.svd(X_new)

In [ ]:
(m,n) = X_new.shape
S_svd = np.zeros((m,n))
S_svd[:m, :m] = np.diag(s)

Reconstruction

In [ ]:
X_rec = U_svd.dot(S_svd.dot(V_svd))

P, Q

In [ ]:
P = U_svd.dot(np.sqrt(S_svd))[:m,:m]
Q = np.sqrt(S_svd).dot(V_svd)

Reconstruisez le signal de départ à partir de P et Q

In [ ]:
imshow(dot(P,Q))

  * Affichez l'utilisateur 300 selon ses deux premières composantes (matrice P). 
  * Affichez également chacun des notes données par cet utilisateurs selon leurs deux premières composantes (matrice Q).
  * Donnez la moyenne des notes cet utilisateur sur chaque quadrant. 
  * Conclusion?

Déterminez les cinq plus proches voisins de l'utilisateur 300 selon les valeurs de la matrice P. Les notes de cet utilisateur sont-elles prédictibles à partir des notes données par les voisins?